In [1]:
#initial imports
import numpy as np
import pandas as pd
import json
from collections import Counter
import re
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
from IPython.display import clear_output
import time
#SpaCy
import spacy
spacy.load('en')
from spacy.lang.en import English
#sklearn
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import Normalizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.cluster import KMeans
from sklearn.preprocessing import normalize
from sklearn.decomposition import PCA
from sklearn.cluster import MiniBatchKMeans
from sklearn import metrics
from sklearn.metrics import confusion_matrix
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.model_selection import cross_val_score
from sklearn import ensemble
from sklearn.decomposition import PCA
from sklearn.cluster import MeanShift
from sklearn.cluster import estimate_bandwidth
from sklearn.cluster import KMeans
from sklearn.cluster import MiniBatchKMeans
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn import neural_network
from sklearn.model_selection import GridSearchCV
from sklearn import ensemble
from sklearn.decomposition import PCA
from sklearn.cluster import MeanShift, estimate_bandwidth
from sklearn.cluster import KMeans, MiniBatchKMeans
from sklearn import metrics
from sklearn.metrics import confusion_matrix
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.model_selection import cross_val_score
from sklearn.utils import shuffle
from sklearn import neural_network
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import CountVectorizer
#BeautifulSoup and NLTK
from bs4 import BeautifulSoup
from nltk.tokenize import WordPunctTokenizer
from nltk.corpus import stopwords # Import the stop word list
from nltk import word_tokenize
from nltk.corpus import wordnet as wn
import nltk
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer
#plotly
import plotly.plotly as py
from plotly.graph_objs import *
import plotly
import plotly.tools as tls
import plotly.graph_objs as go
import plotly.figure_factory as ff
from  plotly  import __version__
#plotly offline
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
print(__version__) # requires version >= 1.9.0
init_notebook_mode(connected=True)
#gensim
import os
import sys
import bz2
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
import multiprocessing
import gensim
from gensim import corpora
from gensim import models
import pickle
import pyLDAvis.gensim
from gensim.models.coherencemodel import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.corpora.dictionary import Dictionary
from numpy import array
from gensim.models import Phrases

3.1.0


2019-02-14 22:22:43,517 : INFO : 'pattern' package not found; tag filters are not available for English


In [2]:
df = pd.read_csv('~/Desktop/Final Capstone/jobs_db.csv')
pd.set_option('display.max_colwidth', -1)

In [3]:
df.head(10)

id  \
0  15   
1  16   
2  17   
3  18   
4  19   
5  20   
6  21   
7  22   
8  23   
9  24   

                                                                                                                                                                                                 title  \
0  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Scientist - Natural Language Processing</h3>                                                                     
1  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Scientist - Natural Language Processing</h3>                                                                     
2  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Scientist - Natural Language Processing</h3>                                                                     
3  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Natural Language Processing Engineer, New York City</h3>                                                                  
4  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Programmer I - Natural Language Processing</h3>                                                                  
5  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Siri - Natural Language Processing Scientist/Engineer</h3>                                                                
6  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">NLP and Machine Learning Graduate</h3>                                                                                    
7  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Data Scientist, Natural Language Processing (NLP), descriptive statistics, statistical modelling, machine learning</h3>   
8  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Software Engineer, Natural Language Processing /NLP</h3>                                                                  
9  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Natural Language Processing and Machine Learning Engineer</h3>                                                            

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

Turn our df into X, for later use with modelling, train_test_split and getting a y column.

In [4]:
X = df

## EDA and Data Cleaning

Since we web scraped, the text is in pretty raw format.  To get it into useable shape, I plan to get rid of the html code before tokenizing and lemmatizing it. I'll also check for duplicates, and remove any to keep the results as clean as possible.  From here, it will be easier to determine what words can be added as stop words, or, are meaningful to the analysis in some way.

In [5]:
#Let's check for unique job descriptions. 
#If we drop some duplicates, we'll run our cleaning on less data, which is faster.
X.nunique()

id                 7882
title              3464
job_description    4334
job_class          9   
dtype: int64

In [6]:
X.job_class.unique()

array(['Natural Language Processing', 'Text Mining',
       'Pattern Recognition', 'Machine Learning', 'Computer Vision',
       'Text Analytics', 'Apache Spark', 'Speech Recognition',
       'Neural Networks'], dtype=object)

In [7]:
X.groupby(X['job_class'])['job_description'].count().sort_values()

job_class
Pattern Recognition            792
Text Analytics                 795
Neural Networks                827
Computer Vision                829
Natural Language Processing    881
Apache Spark                   919
Machine Learning               934
Speech Recognition             944
Text Mining                    961
Name: job_description, dtype: int64

In [8]:
#It stands to reason that we would want to keep the unique job descriptions, because titles like "Data Scientist"
#are broadly used in the field and not necessarily problematic for the scope of this project.
X = X.drop_duplicates(['job_description'], keep = 'last')

In [9]:
#Let's check to make sure we dropped what we had intended.
X.nunique()

id                 4334
title              3431
job_description    4334
job_class          9   
dtype: int64

In [10]:
X.groupby(X['job_class'])['job_description'].count().sort_values()

job_class
Text Analytics                 171
Text Mining                    171
Pattern Recognition            321
Natural Language Processing    510
Machine Learning               573
Computer Vision                633
Apache Spark                   645
Speech Recognition             648
Neural Networks                662
Name: job_description, dtype: int64

The sum of our "female dominated fields is 1,500 which is 34.6% of our dataset. I'm going to drop rows that are Computer Vision job descriptions.  This should help even out the imbalance, and that particular field was the most "gender-balanced" out of the male-dominated job descriptions we have above.

In [11]:
#Dropping Computer Vision
X = X[X.job_class != 'Computer Vision']

In [12]:
X.reset_index(drop=True, inplace=True)

In [13]:
X.head(10)

id  \
0  17   
1  18   
2  19   
3  20   
4  21   
5  29   
6  37   
7  38   
8  44   
9  45   

                                                                                                                                                      title  \
0  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Scientist - Natural Language Processing</h3>                          
1  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Natural Language Processing Engineer, New York City</h3>                       
2  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Programmer I - Natural Language Processing</h3>                       
3  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Siri - Natural Language Processing Scientist/Engineer</h3>                     
4  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">NLP and Machine Learning Graduate</h3>                                         
5  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">AI Research - Natural Language Processing(NLP) Scientist</h3>                  
6  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Analytical Linguist, Google AI</h3>                                            
7  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">IBM Research AI Residency Program</h3>                                         
8  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">AI Research Engineer – Natural Language Processing</h3>                        
9  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Software Engineer: Machine Learning - Natural Language Processing (NLP)</h3>   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [14]:
X.groupby(X['job_class'])['job_description'].count().sort_values()

job_class
Text Analytics                 171
Text Mining                    171
Pattern Recognition            321
Natural Language Processing    510
Machine Learning               573
Apache Spark                   645
Speech Recognition             648
Neural Networks                662
Name: job_description, dtype: int64

Although we lost a large portion of the dataset due to duplicates, it's important to prioritize quality over quantity. I evaluated the dataset to ensure that there would not be a class imbalance problem.  Now, our female-dominated fields comprise 40% of the job descriptions, this is pretty good considering we're working with scraped data. So, we'll proceed with cleaning up the dataset, so we can put it into BoW and Tf-Idf and then run some models on it!

In [15]:
#A quick view of the dataset to see what we might need to clean.
X.head(10)

id  \
0  17   
1  18   
2  19   
3  20   
4  21   
5  29   
6  37   
7  38   
8  44   
9  45   

                                                                                                                                                      title  \
0  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Scientist - Natural Language Processing</h3>                          
1  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Natural Language Processing Engineer, New York City</h3>                       
2  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Research Programmer I - Natural Language Processing</h3>                       
3  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Siri - Natural Language Processing Scientist/Engineer</h3>                     
4  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">NLP and Machine Learning Graduate</h3>                                         
5  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">AI Research - Natural Language Processing(NLP) Scientist</h3>                  
6  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Analytical Linguist, Google AI</h3>                                            
7  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">IBM Research AI Residency Program</h3>                                         
8  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">AI Research Engineer – Natural Language Processing</h3>                        
9  <h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">Software Engineer: Machine Learning - Natural Language Processing (NLP)</h3>   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

Lots of HTML script here, as expected. Let's get some of that cleaned up before we tokenize.

In [16]:
X['job_description'] = X['job_description'].replace(r'div class="jobsearch-JobComponent-description icl-u-xs-mt--md"><div></div><div><div><div><b>', '', regex=True).replace(r'</div', '', regex=True)

In [17]:
X['title'] = X['title'].replace(r'<h3 class="icl-u-xs-mb--xs icl-u-xs-mt--none jobsearch-JobInfoHeader-title">', '', regex=True).replace(r'</h3>', '', regex=True)

In [18]:
X.head(10)

id  \
0  17   
1  18   
2  19   
3  20   
4  21   
5  29   
6  37   
7  38   
8  44   
9  45   

                                                                     title  \
0  Research Scientist - Natural Language Processing                          
1  Natural Language Processing Engineer, New York City                       
2  Research Programmer I - Natural Language Processing                       
3  Siri - Natural Language Processing Scientist/Engineer                     
4  NLP and Machine Learning Graduate                                         
5  AI Research - Natural Language Processing(NLP) Scientist                  
6  Analytical Linguist, Google AI                                            
7  IBM Research AI Residency Program                                         
8  AI Research Engineer – Natural Language Processing                        
9  Software Engineer: Machine Learning - Natural Language Processing (NLP)   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

Much better, our job titles look really nice at this point. Onward!

In [19]:
X['job_description'] = X['job_description'].replace(r'<div class="jobsearch-JobComponent-description icl-u-xs-mt--md">', '', regex=True)


In [20]:
X.sample(10)

id                                              title  \
2330  6072  Data Engineer Technical Lead                        
99    236   Sr. Machine Learning Engineer – Content Knowledge   
3614  7822  Machine Learning Engineer                           
1663  4531  Senior Data Scientist                               
2171  5866  Software Engineer - Distributed Systems             
3424  7603  Experimental Physicist                              
953   2259  Data Scientist, Supply Chain                        
856   2131  Senior Data Scientist Internship - Summer 2019      
1031  2720  Data Science Graduate Internship                    
1955  5588  Hadoop Developer                                    

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [21]:
len(X)

3701

In [22]:
#This will get rid of most of the html markers that are within <>
def clean_html(text):
    """Remove html tags from a string"""
    import re
    clean = re.compile('<.*?>')
    return re.sub(clean, '', text)

In [23]:
for text in X:
    for i in range(len(X)):
        X['job_description'][i] = clean_html(X['job_description'][i])

This took under 10 seconds to run.

In [24]:
X.sample(25)

id                                                              title  \
515   910   Data Scientist                                                      
2483  6285  HSE Coordinator                                                     
3353  7509  Research Scientist                                                  
1224  3126  Machine Learning                                                    
268   533   NLP Engineer with Thai                                              
3360  7521  Process Control Engineer                                            
319   626   Software Engineer: Intern 2019 - Web &amp; Mobile                   
1684  4559  Machine Learning (AI) Software Engineer - Innovation Group          
3214  7298  Senior Data Scientist                                               
1716  4607  Senior Technical Architect                                          
3098  7157  Data &amp; Algorithm Scientist                                      
325   635   Search– Digital Product Manager – CIB – VP                          
1694  4573  Data Scientist                                                      
1023  2705  Machine Learning Engineer                                           
2300  6036  Big Data Streaming Software Engineer - Kafka and AWS                
955   2261  Senior Scientist - Immuno-Oncology, Bioinformatics Data Scientist   
3346  7499  Staff Data Scientist                                                
1912  5530  Commercial Account Executive (New York)                             
2843  6767  Deep Learning Software Engineer - AI Applications                   
242   493   Software Engineer                                                   
3219  7303  Data Scientist, Applied Machine Learning - RNA                      
1627  4489  Senior Director of R&amp;D Data Science Tools                       
3355  7513  Software Engineer Intern                                            
2087  5769  APPLICATION DEVELOPER SR                                            
1548  3562  Data Scientist                                                      

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

That worked like a charm! Let's continue cleaning.

In [25]:
X['job_description'] = X['job_description'].replace(r'\n', '', regex=True)

In [26]:
X.sample(25)

id  \
2599  6443   
587   1040   
2076  5754   
957   2264   
2768  6661   
581   1033   
3178  7257   
2421  6198   
3107  7169   
1463  3461   
327   637    
495   875    
1977  5617   
2093  5775   
960   2267   
1654  4521   
1188  3065   
3661  7870   
3484  7671   
2166  5861   
3597  7804   
3428  7608   
738   1959   
2108  5796   
2944  6920   

                                                                   title  \
2599  Project Manager                                                      
587   Senior Data Scientist                                                
2076  Associate Partner, Cognitive and Analytics - Financial Services      
957   Overnight Security Officer $13.50 SRO Position Full Time             
2768  IT Service Support Specialist                                        
581   Cognitive, Manager- Agile Analytics                                  
3178  Machine Learning Software Developer in Test                          
2421  HR Operations Specialist                                             
3107  Senior Data Scientist                                                
1463  Machine Learning - Feature Engineer - GPShopper                      
327   Data Scientist                                                       
495   Software Engineer, Network Infrastructure, PhD University Graduate   
1977  IT Advisor, Technology Consulting                                    
2093  Senior Software Engineer, Labs                                       
960   Software Engineer, Community Integrity                               
1654  Senior Data Scientist - Open Source                                  
1188  Machine Learning Expert Full Time Only GC Citizens.                  
3661  Customer Data Scientist/Sales Engineer                               
3484  Specialist, Model Development                                        
2166  Senior Data Architect                                                
3597  Principal Data Scientist                                             
3428  Artificial Intelligence Analyst                                      
738   TechStudent-Sophomore                                                
2108  Senior Data Engineer, Audience Studio                                
2944  AM and PM Sous Chef                                                  

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [27]:
X['job_description'] = X['job_description'].replace(r'&amp;', '', regex=True)

In [28]:
X.sample(25)

id  \
1339  3295   
2114  5802   
3485  7672   
2516  6328   
1226  3128   
252   505    
282   552    
2379  6124   
1950  5582   
965   2272   
3060  7110   
1569  3588   
2186  5883   
23    80     
2270  6000   
2205  5909   
1365  3334   
3095  7151   
1511  3519   
3145  7214   
28    90     
2364  6107   
1931  5556   
2883  6849   
1457  3454   

                                                                       title  \
1339  Data Science Graduate Internship - Summer 2019                           
2114  Software Development Engineer                                            
3485  Research Intern, Silicon (PhD University Student)                        
2516  Laundry Attendant                                                        
1226  Distinguished Software Engineer - Machine Learning                       
252   Senior Data Scientist (NLP)                                              
282   Data Technologist - Scientist - United Arab Emirates                     
2379  Cloud Software Engineer: 5 + yrs exp                                     
1950  Labor Systems Projects &amp; Analytics Internship - Orlando, Fall 2019   
965   Targeting and GEOINT Analyst (TS/SCI w/Polygraph)                        
3060  Data Scientist, Machine Learning Engineer                                
1569  Software and Machine Learning Engineer                                   
2186  Software Engineer - Machine Learning - New Frontiers                     
23    AI Research Scientist – Natural Language Processing                      
2270  Mid-Level Data Management Engineer                                       
2205  Senior Software Engineer - Technology                                    
1365  Staff Machine Learning Engineer                                          
3095  Senior Linux Infrastructure Automation Engineer                          
1511  Machine Learning and AI Research Scientist (FY19)                        
3145  Software Engineering Co-Op                                               
28    Data Scientist, Natural Language Processing                              
2364  Data Scientist                                                           
1931  Software Team Lead, Discounts                                            
2883  Kitchen Porter AM/PM                                                     
1457  Data Scientist I/II/III - 014373                                         

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [29]:
X['job_description'] = X['job_description'].replace(r'>', '', regex=True)

In [30]:
X.sample(25)

id  \
753   1980   
3411  7588   
1608  4467   
649   1126   
635   1107   
1638  4503   
1972  5611   
1911  5529   
1684  4559   
2657  6527   
177   361    
536   960    
2828  6748   
755   1982   
1545  3559   
1748  4875   
2791  6691   
2681  6559   
1945  5575   
1348  3306   
1815  5203   
440   803    
3453  7634   
3062  7112   
3673  7882   

                                                                    title  \
753   Postdoctoral Fellowship: Bioprocess Analytics                         
3411  Senior Infrastructure Engineer                                        
1608  Sr. Manager, Decision Analytics Services (Claims Analytics)           
649   Senior Data Scientist (Req. 10062)                                    
635   Data Scientist II                                                     
1638  Senior Analytics Consultant - Clinical Operations                     
1972  Data Engineer - Jr                                                    
1911  Part-Time Faculty - Big Data Analytics (IST718)                       
1684  Machine Learning (AI) Software Engineer - Innovation Group            
2657  Ski Instructors Needed at Giants Ridge Resort                         
177   Artificial Intelligence Engineer                                      
536   Data Scientist                                                        
2828  Mgr, Software Development - Voice Shopping                            
755   Biostatistician                                                       
1545  Machine Learning App Visualization Summer Intern                      
1748  Senior Hadoop / Spark Administrator                                   
2791  Staff Dialogue Systems Engineer (702855)                              
2681  Artificial Intelligence Solution Architect                            
1945  Data Science Intern                                                   
1348  Researcher Opportunities for PhD Students or Recent Graduates         
1815  Full/Associate Professor Tenure System                                
440   Data Solutions Architect I                                            
3453  Enterprise Data Scientist (PERM)                                      
3062  Software Engineer/Research Scientist for Ads - NLP/Knowledge Mining   
3673  Post Doc PET Physicist                                                

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

The last regex left quite a bit of whitespace, which isn't useful. Let's strip that before moving on.

In [31]:
X['job_description'] = X['job_description'].str.strip()

In [32]:
X.sample(25)

id  \
181   366    
1577  4427   
848   2119   
1749  4877   
1415  3402   
2078  5758   
1718  4609   
3029  7054   
1311  3253   
2940  6914   
445   809    
149   317    
2409  6178   
3050  7099   
760   1987   
3654  7863   
1035  2733   
1842  5360   
2262  5991   
2384  6130   
1622  4484   
2661  6531   
1596  4452   
3077  7131   
408   755    

                                                                   title  \
181   Data Scientist                                                       
1577  Social Analytics DATG Internship, Summer 2019 – Burbank, CA          
848   Data Scientist                                                       
1749  Jr. Big Data Developer                                               
1415  Data Science Intern                                                  
2078  Python Developer                                                     
1718  Senior Data Scientist (TS/SCI w/ CI Poly)                            
3029  Physician Ambulatory/Outpatient Primary Care Clinic (Marshalltown)   
1311  Data Analyst - Machine Learning                                      
2940  Corporate Recruiter and Human Resources Business Partner             
445   Software Engineer                                                    
149   Account Manager                                                      
2409  Applied Research Scientist, Speech Recognition Acoustic Modeling     
3050  Senior Applied Scientist                                             
760   Security Officer                                                     
3654  Applied Research Scientist, Core Machine Learning                    
1035  Machine Learning Engineer                                            
1842  Security Data Scientist                                              
2262  Sr. Engineering Manager - Developer Platform                         
2384  AI &amp; Analytics Senior Associate                                  
1622  Sr Analytics Consultant                                              
2661  Collections Loan Counselor I                                         
1596  VOC Analytics Senior Manager                                         
3077  Data Scientist                                                       
408   Machine Learning Scientist - Data Team                               

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [33]:
#We don't need the ids that populated in the SQLite Database
X = X.drop(['id'], axis=1)

In [34]:
X.head(10)

title  \
0  Research Scientist - Natural Language Processing                          
1  Natural Language Processing Engineer, New York City                       
2  Research Programmer I - Natural Language Processing                       
3  Siri - Natural Language Processing Scientist/Engineer                     
4  NLP and Machine Learning Graduate                                         
5  AI Research - Natural Language Processing(NLP) Scientist                  
6  Analytical Linguist, Google AI                                            
7  IBM Research AI Residency Program                                         
8  AI Research Engineer – Natural Language Processing                        
9  Software Engineer: Machine Learning - Natural Language Processing (NLP)   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [35]:
#Let's remove punctuation.
def punctuation_remover(row):
    punctuation = '!"#$&\'()*+,-./:;<=>?@[\\]^_`{|}~«»'  
    
    punctuationNoPeriod = "[" + re.sub("\.","", punctuation) + "]"
    row = re.sub(punctuationNoPeriod, " ", str(row))
    #to remove double white spaces and create space after %,
    row = row.replace('  ', ' ')
    row = row.replace('%', '% ')
    return row.strip()

<input>:5: DeprecationWarning:

invalid escape sequence \.

<input>:5: DeprecationWarning:

invalid escape sequence \.

<input>:5: DeprecationWarning:

invalid escape sequence \.

<ipython-input-35-b2830c59b60e>:5: DeprecationWarning:

invalid escape sequence \.



In [36]:
# remove punctuation from the job titles first
X['title'] = X['title'].apply(punctuation_remover)

In [37]:
X.head(10)

title  \
0  Research Scientist  Natural Language Processing                       
1  Natural Language Processing Engineer New York City                    
2  Research Programmer I  Natural Language Processing                    
3  Siri  Natural Language Processing Scientist Engineer                  
4  NLP and Machine Learning Graduate                                     
5  AI Research  Natural Language Processing NLP Scientist                
6  Analytical Linguist Google AI                                         
7  IBM Research AI Residency Program                                     
8  AI Research Engineer – Natural Language Processing                    
9  Software Engineer Machine Learning  Natural Language Processing NLP   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [38]:
#Since that worked well, let's now remove punctuation from the job descriptions.
X['job_description'] = X['job_description'].apply(punctuation_remover)

In [39]:
X.head(10)

title  \
0  Research Scientist  Natural Language Processing                       
1  Natural Language Processing Engineer New York City                    
2  Research Programmer I  Natural Language Processing                    
3  Siri  Natural Language Processing Scientist Engineer                  
4  NLP and Machine Learning Graduate                                     
5  AI Research  Natural Language Processing NLP Scientist                
6  Analytical Linguist Google AI                                         
7  IBM Research AI Residency Program                                     
8  AI Research Engineer – Natural Language Processing                    
9  Software Engineer Machine Learning  Natural Language Processing NLP   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [40]:
X['gender_breakdown'] = X['job_class']

In [41]:
X.job_class.unique()

array(['Natural Language Processing', 'Text Mining',
       'Pattern Recognition', 'Machine Learning', 'Text Analytics',
       'Apache Spark', 'Speech Recognition', 'Neural Networks'],
      dtype=object)

In [42]:
X.loc[X['gender_breakdown'] == 'Natural Language Processing', 'gender_breakdown'] = 1
X.loc[X['gender_breakdown'] == 'Text Mining', 'gender_breakdown'] = 1
X.loc[X['gender_breakdown'] == 'Text Analytics', 'gender_breakdown'] = 1
X.loc[X['gender_breakdown'] == 'Speech Recognition', 'gender_breakdown'] = 1
X.loc[X['gender_breakdown'] == 'Pattern Recognition', 'gender_breakdown'] = 0
X.loc[X['gender_breakdown'] == 'Machine Learning', 'gender_breakdown'] = 0
X.loc[X['gender_breakdown'] == 'Apache Spark', 'gender_breakdown'] = 0
X.loc[X['gender_breakdown'] == 'Neural Networks', 'gender_breakdown'] = 0

In [43]:
X.sample(5)

title  \
706   Equipment  Maintenance Technician   
58    Sales Associate                     
2142  Senior Data Engineer                
4     NLP and Machine Learning Graduate   
2181  Data Engineer                       

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               

## Unsupervised Approach

I'll use the Latend Dirichlet Allocation method first, and then use it with bigrams and trigrams. I will evalute for coherence, and tune the models.

In [44]:
#First step, tokenizer.
parser = English()
def tokenize(text):
    lda_tokens = []
    tokens = parser(text)
    for token in tokens:
        if token.orth_.isspace():
            continue
        elif token.like_url:
            lda_tokens.append('URL')
        else:
            lda_tokens.append(token.lower_)
    return lda_tokens

In [45]:
nltk.download('wordnet')
def get_lemma(word):
    lemma = wn.morphy(word)
    if lemma is None:
        return word
    else:
        return lemma
    
from nltk.stem.wordnet import WordNetLemmatizer
def get_lemma2(word):
    return WordNetLemmatizer().lemmatize(word)

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/tiffanyfrench/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [46]:
#nltk.download('stopwords')
en_stop = set(nltk.corpus.stopwords.words('english'))
stopwords = en_stop.union(set(['machine','business','analytics','learning','technology',
                              'system']))

In [47]:
def prepare_text_for_lda(text):
    tokens = tokenize(text)
    tokens = [token for token in tokens if len(token) > 4]
    tokens = [token for token in tokens if token not in en_stop]
    tokens = [get_lemma(token) for token in tokens]
    return tokens

In [48]:
import random
text_data = []
for text in X:
    for i in range(len(X)):
        tokens = prepare_text_for_lda(X['job_description'][i])
        if random.random() > .99:
            print(tokens)
            text_data.append(tokens)

['timedepartment', 'platform', 'researchjd', 'research', 'looking', 'notch', 'research', 'scientist', 'silicon', 'valley', 'excite', 'opportunity', 'early', 'stage', 'variety', 'research', 'area', 'natural', 'language', 'processing', 'include', 'natural', 'language', 'understanding', 'natural', 'language', 'generation', 'speak', 'dialog', 'system', 'question', 'answer', 'machine', 'reading', 'comprehension', 'responsibility', 'define', 'ambitious', 'relevant', 'research', 'problem', 'criterion', 'evaluate', 'success', 'build', 'state', 'solution', 'designing', 'algorithm', 'carry', 'experiment', 'engineering', 'team', 'appropriate', 'solution', 'publish', 'notch', 'conferencesqualifications', 'master', 'degree', 'computer', 'science', 'relate', 'field', 'ability', 'communicate', 'collaborate', 'researcher', 'engineer', 'include', 'member', 'china', 'ability', 'speak', 'chinese', 'require', 'ability', 'implement', 'experiment', 'using', 'script', 'language', 'python', 'tool', 'write', '

['overviewsearching', 'experience', 'architect', 'mature', 'company', 'architecture', 'management', 'practice', 'guide', 'application', 'platforming', 'decision', 'labcorp', 'currently', 'working', 'major', 'effort', 'reengineer', 'revenue', 'process', 'develop', 'patient', 'centric', 'focus', 'across', 'company', 'initiative', 'department', 'playing', 'retool', 'cutting', 'technology', 'development', 'process', 'architect', 'member', 'overall', 'logical', 'design', 'information', 'model', 'integration', 'disparate', 'source', 'development', 'team', 'merge', 'legacy', 'system', 'architecture', 'summary', 'positionlabcorp', 'looking', 'hands', 'analyst', 'technologist', 'architect', 'experience', 'enterprise', 'architecture', 'information', 'management', 'governance', 'warehousing', 'analytics', 'technology', 'provide', 'tactical', 'strategic', 'direction', 'area', 'standardization', 'governance', 'quality', 'strategy', 'lifecycle', 'management', 'business', 'intelligence', 'analytics',

['responsibilitiescandidate', 'provide', 'advance', 'creative', 'technical', 'consult', 'identity', 'management', 'technology', 'enhance', 'border', 'security', 'screening', 'manage', 'identity', 'travel', 'document', 'applicant', 'candidate', 'understanding', 'capability', 'exist', 'emerge', 'research', 'develop', 'engineer', 'evaluate', 'implement', 'solution', 'enhance', 'border', 'security', 'screening', 'vet', 'mission', 'responsibility', 'engineer', 'solution', 'optimize', 'monitor', 'measure', 'accuracy', 'large', 'scale', 'government', 'operational', 'recognition', 'systemanalyze', 'national', 'international', 'biometrics', 'standard', 'propose', 'standard', 'policy', 'would', 'affect', 'processing', 'visa', 'passportsresearch', 'measure', 'capability', 'various', 'type', 'biometric', 'sample', 'capture', 'imaging', 'equipment', 'various', 'modality', 'biometric', 'identification', 'softwaredevelop', 'alternate', 'concept', 'operation', 'improve', 'biometric', 'sample', 'image'

['masters', 'degree', 'computer', 'science', 'engineering', 'mathematics', 'relate', 'discipline', 'least', 'years', 'experience', 'machine', 'learning', 'system', 'least', 'years', 'experience', 'building', 'base', 'production', 'software', 'hands', 'development', 'experience', 'python', 'amazon', 'equal', 'opportunity', 'affirmative', 'action', 'employer', 'minority', 'female', 'disability', 'veteran', 'gender', 'identity', 'sexual', 'orientationthe', 'amazon', 'search', 'create', 'powerful', 'customer', 'focus', 'search', 'advertising', 'solution', 'technology', 'whenever', 'customer', 'visit', 'amazon', 'worldwide', 'type', 'query', 'browse', 'product', 'category', 'amazon', 'search', 'services', 'design', 'develop', 'deploy', 'performance', 'fault', 'tolerant', 'distribute', 'search', 'system', 'million', 'amazon', 'customer', 'every', 'search', 'relevance', 'works', 'maximize', 'quality', 'effectiveness', 'search', 'experience', 'visitor', 'amazon', 'website', 'worldwide', 'produ

['http', 'lever', 'client', 'logos', 'amazonaws', 'b67910ec', '9bf219ea7d50', '1495723288350', 'analystnew', 'nyfull', 'timemoneylion', 'leading', 'mobile', 'finance', 'platform', 'empower', 'consumer', 'control', 'financial', 'life', 'spending', 'saving', 'credit', 'tracking', 'tool', 'smart', 'credit', 'product', 'found', 'leading', 'technologist', 'financier', 'moneylion', 'superior', 'analytics', 'machine', 'learning', 'base', 'technology', 'degree', 'users’', 'personal', 'finances', 'enable', 'better', 'underwrite', 'development', 'tailor', 'financial', 'product', 'offer', 'build', 'system', 'social', 'endorsement', 'loyalty', 'point', 'reward', 'moneylion', 'endorse', 'financial', 'behavior', 'habit', 'building', 'looking', 'forwe', 'looking', 'analyst', 'analytics', 'drive', 'approach', 'growth', 'looking', 'someone', 'hands', 'approach', 'tracking', 'experimentation', 'optimization', 'someone', 'willing', 'spend', 'grasp', 'understanding', 'business', 'vertical', 'product', 'cr

...

['zipcar', 'world', 'leading', 'sharing', 'network', 'drive', 'city', 'better', 'place', 'since', 'work', 'brilliant', 'disruptive', 'movement', 'serve', 'million', 'member', 'worldwide', 'keeping', 'pedal', 'metal', 'growing', 'every', 'talented', 'passionate', 'people', 'great', 'idea', 'zipcar', 'family', 'technologyat', 'zipcar', 'building', 'sharing', 'cloud', 'platform', 'using', 'cutting', 'technology', 'engineer', 'build', 'development', 'process', 'speed', 'market', 'microservice', 'architecture', 'using', 'rabbitmq', 'internal', 'communication', 'services', 'mainly', 'write', 'groovy', 'kotlin', 'rubyresponsive', 'client', 'application', 'build', 'reactjs', 'redux', 'typescriptnative', 'mobile', 'application', 'android', 'ioscontinuous', 'integration', 'deployment', 'using', 'technology', 'include', 'concourse', 'docker', 'boshdata', 'technology', 'lake', 'cassandra', 'apache', 'spark', 'inform', 'business', 'decisionsresponsibilitieslead', 'manage', 'software', 'engineering'

['adversary', 'cybercriminals', 'cyber', 'terrorist', 'working', 'every', 'every', 'develop', 'means', 'compromise', 'network', 'seize', 'valuable', 'intellectual', 'property', 'personal', 'advantage', 'digital', 'battlefield', 'northrop', 'grumman', 'mission', 'speed', 'stealth', 'precision', 'control', 'physical', 'domain', 'space', 'imperative', 'control', 'cyber', 'domain', 'talented', 'employee', 'advance', 'every', 'base', 'imperative', 'commit', 'provide', 'advance', 'protection', 'customer', 'rapidly', 'evolve', 'cyber', 'threat', 'spectrum', 'company', 'trust', 'secure', 'system', 'continue', 'trust', 'provider', 'mission', 'enable', 'solution', 'security', 'nation', 'allies', 'without', 'doubt', 'excite', 'times', 'experience', 'value', 'performance', 'northrop', 'grumman', 'mission', 'system', 'seeking', 'multiple', 'cyber', 'software', 'engineer', 'various', 'level', 'qualify', 'diverse', 'individual', 'locate', 'annapolis', 'junction', 'role', 'responsibility', 'include', 

['internshipare', 'highly', 'motivate', 'looking', 'entrepreneurial', 'thinking', 'creative', 'idea', 'internship', 'loancare', 'provider', 'mortgage', 'services', 'industry', 'excite', 'opportunity', 'project', 'base', 'intern', 'opportunity', 'allow', 'intern', 'develop', 'skill', 'necessary', 'placement', 'advancement', 'mortgage', 'financial', 'services', 'industry', 'intern', 'integrate', 'academic', 'theory', 'principle', 'practical', 'experience', 'professional', 'development', 'reinforce', 'expand', 'classroom', 'learning', 'prepare', 'postgraduate', 'employment', 'ready', 'reward', 'opportunity', 'develop', 'professional', 'strongly', 'encourage', 'apply', 'today', 'become', 'something', 'lifein', 'create', 'transfer', 'smart', 'training', 'assist', 'operations', 'create', 'submit', 'form', 'accounting', 'processing', 'audit', 'training', 'accounting', 'policy', 'procedure', 'consistency', 'assist', 'daily', 'processing', 'balance', 'sheet', 'balance', 'sheet', 'transactions',

['great', 'people', 'great', 'benefit', 'teampantry', 'lineascending', 'level', 'rainy', 'iconic', 'point', 'washington', 'landscape', 'associate', 'valuable', 'experience', 'meeting', 'guest', 'coworkers', 'around', 'world', 'magical', 'world', 'pristine', 'mountain', 'meadow', 'majestic', 'waterfall', 'peaceful', 'growth', 'forest', 'explore', 'throughout', 'season', 'regularly', 'schedule', 'activity', 'trip', 'transportation', 'provide', 'associate', 'include', 'trip', 'nearby', 'adventure', 'city', 'seattle', 'visit', 'place', 'catch', 'mariner', 'employee', 'vehicle', 'short', 'explore', 'destination', 'portland', 'seattle', 'unique', 'location', 'board', 'provide', 'associate', 'surround', 'community', 'payroll', 'deduction', 'laundry', 'facility', 'provide', 'employee', 'employee', 'meal', 'serve', 'employee', 'dining', 'rooms', 'accommodate', 'limited', 'number', 'unit', 'fully', 'contain', 'camper', 'shell', 'member', 'rainy', 'national', 'expect', 'season', 'approximately', 

['descriptionthe', 'opportunity', 'analytics', 'everywhere', 'solve', 'problem', 'analytics', 'stay', 'forefront', 'artificial', 'intelligence', 'machine', 'learning', 'build', 'something', 'meaningful', 'using', 'cutting', 'technology', 'build', 'industry', 'leading', 'solution', 'problem', 'solver', 'solving', 'tough', 'problem', 'analytics', 'world', 'situation', 'thrive', 'opportunity', 'bright', 'analytical', 'engineering', 'mind', 'industry', 'share', 'passion', 'innovation', 'director', 'analytic', 'sciencewhat', 'contributework', 'large', 'amount', 'world', 'nsure', 'quality', 'throughout', 'stage', 'acquisition', 'processing', 'include', 'collection', 'normalization', 'transformation', 'research', 'select', 'appropriate', 'statistical', 'method', 'computational', 'algorithm', 'build', 'oversee', 'team', 'building', 'analytic', 'model', 'relevant', 'problem', 'using', 'statistical', 'modeling', 'technique', 'manage', 'project', 'constraint', 'working', 'team', 'within', 'provid

In [49]:
# Using Gensim to bolster NLTK

In [50]:
dictionary = corpora.Dictionary(text_data)

2019-02-14 22:27:41,724 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2019-02-14 22:27:41,779 : INFO : built Dictionary(6167 unique tokens: ['ability', 'additional', 'algorithm', 'ambitious', 'answer']...) from 151 documents (total 42770 corpus positions)


In [51]:
## Remove words occuring less than 20 times, and words occuring in more than 10% of the documents. 
#dictionary = dictionary.filter_extremes(no_below=20, no_above=0.1)
#dictionary.filter_extremes (
#no_below= 20,
#no_above= 0.1#,
#keep_n: int=100000,
#keep_tokens: NoneType=None
#)

In [52]:
corpus = [dictionary.doc2bow(text) for text in text_data]

In [53]:
pickle.dump(corpus, open('corpus.pkl', 'wb'))
dictionary.save('dictionary.gensim')

2019-02-14 22:27:41,907 : INFO : saving Dictionary object under dictionary.gensim, separately None
2019-02-14 22:27:41,925 : INFO : saved dictionary.gensim


In [54]:
## Remove words occuring less than 20 times, and words occuring in more than 10% of the documents. 
#dictionary = dictionary.filter_extremes(no_below=20, no_above=0.1)
#filter_extremes (
#no_below: int=20,
#no_above: float=0.1#,
#keep_n: int=100000,
#keep_tokens: NoneType=None
#)

In [55]:
#print(corpus)

In [56]:
NUM_TOPICS = 5
ldamodel = gensim.models.ldamodel.LdaModel(corpus, num_topics = NUM_TOPICS, id2word=dictionary, passes=15)
ldamodel.save('model5.gensim')
topics = ldamodel.print_topics(num_words=4)
for topic in topics:
    print(topic)

2019-02-14 22:27:41,954 : INFO : using symmetric alpha at 0.2
2019-02-14 22:27:41,955 : INFO : using symmetric eta at 0.2
2019-02-14 22:27:41,959 : INFO : using serial LDA version on this node
2019-02-14 22:27:41,969 : INFO : running online (multi-pass) LDA training, 5 topics, 15 passes over the supplied corpus of 151 documents, updating model once every 151 documents, evaluating perplexity every 151 documents, iterating 50x with a convergence threshold of 0.001000
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/s

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

2019-02-14 22:27:42,472 : INFO : PROGRESS: pass 0, at document #151/151
2019-02-14 22:27:42,659 : INFO : topic #0 (0.200): 0.012*"experience" + 0.007*"learning" + 0.007*"technology" + 0.006*"research" + 0.006*"ability" + 0.005*"business" + 0.005*"include" + 0.005*"system" + 0.004*"solution" + 0.004*"problem"
2019-02-14 22:27:42,660 : INFO : topic #1 (0.200): 0.011*"experience" + 0.008*"learning" + 0.007*"science" + 0.005*"system" + 0.005*"machine" + 0.005*"include" + 0.005*"software" + 0.005*"technology" + 0.005*"analytics" + 0.005*"customer"
2019-02-14 22:27:42,662 : INFO : topic #2 (0.200): 0.016*"experience" + 0.007*"learning" + 0.006*"technology" + 0.006*"include" + 0.006*"development" + 0.006*"ability" + 0.006*"software" + 0.005*"system" + 0.005*"machine" + 0.005*"customer"
2019-02-14 22:27:42,664 : INFO : topic #3 (0.200): 0.010*"experience" + 0.007*"customer" + 0.006*"ability" + 0.005*"include" + 0.005*"learning" + 0.005*"software" + 0.005*"research" + 0.004*"information" + 0.00

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

...

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

2019-02-14 22:27:49,030 : INFO : PROGRESS: pass 13, at document #151/151
2019-02-14 22:27:49,145 : INFO : topic #0 (0.200): 0.010*"ability" + 0.008*"experience" + 0.006*"problem" + 0.006*"information" + 0.005*"skill" + 0.005*"include" + 0.005*"customer" + 0.005*"opportunity" + 0.004*"research" + 0.004*"technology"
2019-02-14 22:27:49,146 : INFO : topic #1 (0.200): 0.012*"research" + 0.012*"learning" + 0.010*"science" + 0.008*"system" + 0.007*"experience" + 0.006*"machine" + 0.006*"language" + 0.006*"computer" + 0.005*"include" + 0.005*"technology"
2019-02-14 22:27:49,147 : INFO : topic #2 (0.200): 0.021*"experience" + 0.009*"software" + 0.008*"technology" + 0.008*"learning" + 0.008*"development" + 0.007*"business" + 0.007*"product" + 0.007*"years" + 0.006*"solution" + 0.006*"customer"
2019-02-14 22:27:49,149 : INFO : topic #3 (0.200): 0.013*"ability" + 0.006*"include" + 0.005*"quality" + 0.005*"customer" + 0.005*"skill" + 0.005*"require" + 0.005*"provide" + 0.005*"knowledge" + 0.004*"p

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

2019-02-14 22:27:49,524 : INFO : PROGRESS: pass 14, at document #151/151
2019-02-14 22:27:49,654 : INFO : topic #0 (0.200): 0.010*"ability" + 0.007*"experience" + 0.006*"problem" + 0.006*"information" + 0.005*"skill" + 0.005*"include" + 0.005*"customer" + 0.005*"opportunity" + 0.004*"research" + 0.004*"technology"
2019-02-14 22:27:49,655 : INFO : topic #1 (0.200): 0.013*"research" + 0.012*"learning" + 0.010*"science" + 0.008*"system" + 0.007*"experience" + 0.006*"machine" + 0.006*"language" + 0.006*"computer" + 0.005*"include" + 0.005*"technology"
2019-02-14 22:27:49,656 : INFO : topic #2 (0.200): 0.021*"experience" + 0.009*"software" + 0.008*"technology" + 0.008*"learning" + 0.008*"development" + 0.007*"business" + 0.007*"product" + 0.007*"years" + 0.006*"solution" + 0.006*"customer"
2019-02-14 22:27:49,658 : INFO : topic #3 (0.200): 0.013*"ability" + 0.006*"include" + 0.005*"quality" + 0.005*"customer" + 0.005*"require" + 0.005*"provide" + 0.005*"skill" + 0.005*"knowledge" + 0.004*"p

(0, '0.010*"ability" + 0.007*"experience" + 0.006*"problem" + 0.006*"information"')
(1, '0.013*"research" + 0.012*"learning" + 0.010*"science" + 0.008*"system"')
(2, '0.021*"experience" + 0.009*"software" + 0.008*"technology" + 0.008*"learning"')
(3, '0.013*"ability" + 0.006*"include" + 0.005*"quality" + 0.005*"customer"')
(4, '0.012*"business" + 0.010*"analytics" + 0.007*"insight" + 0.007*"customer"')


In [57]:
dictionary = gensim.corpora.Dictionary.load('dictionary.gensim')
corpus = pickle.load(open('corpus.pkl', 'rb'))
lda = gensim.models.ldamodel.LdaModel.load('model5.gensim')
import pyLDAvis.gensim
lda_display = pyLDAvis.gensim.prepare(lda, corpus, dictionary, sort_topics=False)
pyLDAvis.display(lda_display)

2019-02-14 22:27:49,799 : INFO : loading Dictionary object from dictionary.gensim
2019-02-14 22:27:49,808 : INFO : loaded dictionary.gensim
2019-02-14 22:27:49,821 : INFO : loading LdaModel object from model5.gensim
2019-02-14 22:27:49,831 : INFO : loading expElogbeta from model5.gensim.expElogbeta.npy with mmap=None
2019-02-14 22:27:49,833 : INFO : setting ignored attribute dispatcher to None
2019-02-14 22:27:49,833 : INFO : setting ignored attribute state to None
2019-02-14 22:27:49,834 : INFO : setting ignored attribute id2word to None
2019-02-14 22:27:49,835 : INFO : loaded model5.gensim
2019-02-14 22:27:49,836 : INFO : loading LdaState object from model5.gensim.state
2019-02-14 22:27:49,838 : INFO : loaded model5.gensim.state
/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retai

In [58]:
ldamodel = gensim.models.ldamodel.LdaModel(corpus, num_topics = 10, id2word=dictionary, passes=15)
ldamodel.save('model10.gensim')
topics = ldamodel.print_topics(num_words=4)
for topic in topics:
    print(topic)

2019-02-14 22:27:55,246 : INFO : using symmetric alpha at 0.1
2019-02-14 22:27:55,248 : INFO : using symmetric eta at 0.1
2019-02-14 22:27:55,252 : INFO : using serial LDA version on this node
2019-02-14 22:27:55,261 : INFO : running online (multi-pass) LDA training, 10 topics, 15 passes over the supplied corpus of 151 documents, updating model once every 151 documents, evaluating perplexity every 151 documents, iterating 50x with a convergence threshold of 0.001000
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

2019-02-14 22:27:55,806 : INFO : PROGRESS: pass 0, at document #151/151
2019-02-14 22:27:56,047 : INFO : topic #7 (0.100): 0.013*"experience" + 0.008*"research" + 0.006*"include" + 0.006*"solution" + 0.006*"system" + 0.005*"customer" + 0.005*"software" + 0.005*"science" + 0.005*"provide" + 0.004*"technology"
2019-02-14 22:27:56,049 : INFO : topic #0 (0.100): 0.012*"experience" + 0.007*"ability" + 0.007*"learning" + 0.006*"research" + 0.006*"customer" + 0.005*"analysis" + 0.005*"business" + 0.005*"analytics" + 0.005*"include" + 0.005*"technology"
2019-02-14 22:27:56,050 : INFO : topic #5 (0.100): 0.016*"experience" + 0.009*"learning" + 0.008*"system" + 0.007*"technology" + 0.007*"customer" + 0.006*"product" + 0.006*"years" + 0.005*"solution" + 0.005*"software" + 0.005*"machine"
2019-02-14 22:27:56,052 : INFO : topic #1 (0.100): 0.009*"learning" + 0.009*"experience" + 0.007*"analytics" + 0.007*"business" + 0.006*"include" + 0.006*"customer" + 0.006*"machine" + 0.005*"science" + 0.005*"te

...

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin in

2019-02-14 22:28:03,198 : INFO : PROGRESS: pass 14, at document #151/151
2019-02-14 22:28:03,321 : INFO : topic #2 (0.100): 0.008*"learning" + 0.006*"machine" + 0.006*"technology" + 0.005*"driving" + 0.005*"dental" + 0.005*"robotics" + 0.004*"student" + 0.004*"tool" + 0.004*"world" + 0.004*"employee"
2019-02-14 22:28:03,323 : INFO : topic #6 (0.100): 0.013*"ability" + 0.011*"experience" + 0.007*"customer" + 0.006*"information" + 0.006*"problem" + 0.006*"include" + 0.005*"skill" + 0.005*"product" + 0.005*"business" + 0.005*"knowledge"
2019-02-14 22:28:03,324 : INFO : topic #3 (0.100): 0.006*"ability" + 0.005*"environment" + 0.005*"minimum" + 0.005*"immune" + 0.005*"transplant" + 0.004*"research" + 0.004*"qualification" + 0.004*"tumor" + 0.003*"computer" + 0.003*"candidate"
2019-02-14 22:28:03,326 : INFO : topic #7 (0.100): 0.011*"research" + 0.011*"experience" + 0.007*"information" + 0.006*"position" + 0.006*"center" + 0.006*"people" + 0.006*"business" + 0.006*"provide" + 0.006*"technol

(0, '0.010*"research" + 0.008*"analysis" + 0.008*"experience" + 0.008*"analytics"')
(1, '0.012*"learning" + 0.012*"science" + 0.011*"research" + 0.008*"experience"')
(2, '0.008*"learning" + 0.006*"machine" + 0.006*"technology" + 0.005*"driving"')
(3, '0.006*"ability" + 0.005*"environment" + 0.005*"minimum" + 0.005*"immune"')
(4, '0.021*"experience" + 0.012*"software" + 0.011*"learning" + 0.010*"development"')
(5, '0.015*"experience" + 0.012*"system" + 0.007*"software" + 0.007*"engineering"')
(6, '0.013*"ability" + 0.011*"experience" + 0.007*"customer" + 0.006*"information"')
(7, '0.011*"research" + 0.011*"experience" + 0.007*"information" + 0.006*"position"')
(8, '0.016*"analytics" + 0.012*"experience" + 0.011*"business" + 0.008*"customer"')
(9, '0.009*"practice" + 0.007*"require" + 0.007*"learning" + 0.006*"resident"')


In [59]:
dictionary = gensim.corpora.Dictionary.load('dictionary.gensim')
corpus = pickle.load(open('corpus.pkl', 'rb'))
lda = gensim.models.ldamodel.LdaModel.load('model10.gensim')
import pyLDAvis.gensim
lda_display = pyLDAvis.gensim.prepare(lda, corpus, dictionary, sort_topics=False)
pyLDAvis.display(lda_display)

2019-02-14 22:28:03,415 : INFO : loading Dictionary object from dictionary.gensim
2019-02-14 22:28:03,421 : INFO : loaded dictionary.gensim
2019-02-14 22:28:03,440 : INFO : loading LdaModel object from model10.gensim
2019-02-14 22:28:03,442 : INFO : loading expElogbeta from model10.gensim.expElogbeta.npy with mmap=None
2019-02-14 22:28:03,444 : INFO : setting ignored attribute dispatcher to None
2019-02-14 22:28:03,446 : INFO : setting ignored attribute state to None
2019-02-14 22:28:03,447 : INFO : setting ignored attribute id2word to None
2019-02-14 22:28:03,447 : INFO : loaded model10.gensim
2019-02-14 22:28:03,448 : INFO : loading LdaState object from model10.gensim.state
2019-02-14 22:28:03,452 : INFO : loaded model10.gensim.state
/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To 

In [60]:
import warnings
warnings.filterwarnings('ignore')  # To ignore all warnings that arise here to enhance clarity
# Convert to array
docs =array(X['job_description'])

In [61]:
# Define function for tokenize and lemmatizing
def docs_preprocessor(docs):
    tokenizer = RegexpTokenizer(r'\w+')
    for idx in range(len(docs)):
        docs[idx] = docs[idx].lower()  # Convert to lowercase.
        docs[idx] = tokenizer.tokenize(docs[idx])  # Split into words.

    # Remove numbers, but not words that contain numbers.
    docs = [[token for token in doc if not token.isdigit()] for doc in docs]
    
    # Remove words that are only one character.
    docs = [[token for token in doc if len(token) > 3] for doc in docs]
    
    # Lemmatize all words in documents.
    lemmatizer = WordNetLemmatizer()
    docs = [[lemmatizer.lemmatize(token) for token in doc] for doc in docs]
  
    return docs

In [62]:
# Perform function on our document
docs = docs_preprocessor(docs)

In [63]:
# Create Biagram & Trigram Models 
# Add bigrams and trigrams to docs,minimum count 10 means only that appear 10 times or more.
bigram = Phrases(docs, min_count=10)
trigram = Phrases(bigram[docs])

for idx in range(len(docs)):
    for token in bigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)
    for token in trigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)

2019-02-14 22:28:11,671 : INFO : collecting all words and their counts
2019-02-14 22:28:11,673 : INFO : PROGRESS: at sentence #0, processed 0 words and 0 word types
2019-02-14 22:28:14,414 : INFO : collected 480173 word types from a corpus of 1301374 words (unigram + bigrams) and 3701 sentences
2019-02-14 22:28:14,414 : INFO : using 480173 counts as vocab in Phrases<0 vocab, min_count=10, threshold=10.0, max_vocab_size=40000000>
2019-02-14 22:28:14,415 : INFO : collecting all words and their counts
2019-02-14 22:28:14,420 : INFO : PROGRESS: at sentence #0, processed 0 words and 0 word types
2019-02-14 22:28:22,001 : INFO : collected 528728 word types from a corpus of 1118780 words (unigram + bigrams) and 3701 sentences
2019-02-14 22:28:22,002 : INFO : using 528728 counts as vocab in Phrases<0 vocab, min_count=5, threshold=10.0, max_vocab_size=40000000>


In [64]:
# Remove rare & common tokens 
# Create a dictionary representation of the documents.
dictionary = Dictionary(docs)
dictionary.filter_extremes(no_below=10, no_above=0.2)

2019-02-14 22:28:32,892 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2019-02-14 22:28:34,682 : INFO : built Dictionary(58551 unique tokens: ['able', 'about', 'abreast', 'access', 'accommodation']...) from 3701 documents (total 1871869 corpus positions)
2019-02-14 22:28:34,855 : INFO : discarding 47371 tokens: [('able', 841), ('about', 1460), ('algorithm', 1347), ('analysis', 1637), ('analytics', 1354), ('applicant', 1185), ('application', 1742), ('apply', 1012), ('approach', 800), ('area', 1276)]...
2019-02-14 22:28:34,856 : INFO : keeping 11180 tokens which were in no less than 10 and no more than 740 (=20.0%) documents
2019-02-14 22:28:34,884 : INFO : resulting dictionary: Dictionary(11180 unique tokens: ['abreast', 'access', 'accommodation', 'accommodation_apply', 'accommodation_request']...)


In [65]:
#Create dictionary and corpus required for Topic Modeling
corpus = [dictionary.doc2bow(doc) for doc in docs]
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))
print(corpus[:1])

Number of unique tokens: 11180
Number of documents: 3701
[[(0, 1), (1, 1), (2, 3), (3, 1), (4, 3), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 3), (14, 1), (15, 1), (16, 2), (17, 6), (18, 1), (19, 1), (20, 2), (21, 1), (22, 1), (23, 1), (24, 1), (25, 3), (26, 1), (27, 3), (28, 1), (29, 1), (30, 2), (31, 3), (32, 1), (33, 1), (34, 1), (35, 3), (36, 1), (37, 1), (38, 3), (39, 2), (40, 1), (41, 1), (42, 4), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 3), (55, 1), (56, 1), (57, 1), (58, 2), (59, 1), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1), (65, 2), (66, 1), (67, 3), (68, 1), (69, 2), (70, 3), (71, 1), (72, 1), (73, 1), (74, 1), (75, 1), (76, 1), (77, 3), (78, 1), (79, 1), (80, 1), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 2), (89, 4), (90, 1), (91, 2), (92, 1), (93, 1), (94, 1), (95, 1), (96, 1), (97, 1), (98, 1), (99, 1), (100, 1), (101, 2), (102, 1), (103, 2), (104, 1), (

In [66]:
# Set parameters.
num_topics = 5
chunksize = 500 
passes = 20 
iterations = 400
eval_every = 1  

In [67]:
# Make a index to word dictionary.
temp = dictionary[0]  # only to "load" the dictionary.
id2word = dictionary.id2token

lda_model = LdaModel(corpus=corpus, id2word=id2word, chunksize=chunksize, \
                       alpha='auto', eta='auto', \
                       iterations=iterations, num_topics=num_topics, \
                       passes=passes, eval_every=eval_every)

2019-02-14 22:28:36,063 : INFO : using autotuned alpha, starting with [0.2, 0.2, 0.2, 0.2, 0.2]
2019-02-14 22:28:36,067 : INFO : using serial LDA version on this node
2019-02-14 22:28:36,075 : INFO : running online (multi-pass) LDA training, 5 topics, 20 passes over the supplied corpus of 3701 documents, updating model once every 500 documents, evaluating perplexity every 500 documents, iterating 400x with a convergence threshold of 0.001000
2019-02-14 22:28:39,645 : INFO : -9.856 per-word bound, 926.8 perplexity estimate based on a held-out corpus of 500 documents with 123968 words
2019-02-14 22:28:39,645 : INFO : PROGRESS: pass 0, at document #500/3701
2019-02-14 22:28:42,839 : INFO : optimized alpha [0.057013467, 0.12923673, 0.050630644, 0.0968365, 0.08257204]
2019-02-14 22:28:42,840 : INFO : merging changes from 500 documents into a model of 3701 documents
2019-02-14 22:28:42,847 : INFO : topic #0 (0.057): 0.005*"data_scientist" + 0.004*"open_source" + 0.003*"artificial_intelligenc

2019-02-14 22:28:52,034 : INFO : -10.156 per-word bound, 1141.3 perplexity estimate based on a held-out corpus of 500 documents with 149973 words
2019-02-14 22:28:52,035 : INFO : PROGRESS: pass 0, at document #2500/3701
2019-02-14 22:28:52,822 : INFO : optimized alpha [0.1290826, 0.32658765, 0.13812852, 0.20724699, 0.18545128]
2019-02-14 22:28:52,822 : INFO : merging changes from 500 documents into a model of 3701 documents
2019-02-14 22:28:52,829 : INFO : topic #0 (0.129): 0.004*"open_source" + 0.003*"data_scientist" + 0.003*"apache" + 0.003*"familiarity_with" + 0.003*"real_time" + 0.002*"this_position" + 0.002*"without_regard" + 0.002*"hand_experience" + 0.002*"apache_hadoop" + 0.002*"bachelor_degree"
2019-02-14 22:28:52,830 : INFO : topic #1 (0.327): 0.005*"data_scientist" + 0.003*"best_practice" + 0.003*"data_visualization" + 0.003*"data_mining" + 0.003*"this_role" + 0.002*"this_position" + 0.002*"advanced_analytics" + 0.002*"health" + 0.002*"bachelor_degree" + 0.002*"sale"
2019-02

2019-02-14 22:28:59,056 : INFO : topic #1 (0.458): 0.005*"data_scientist" + 0.004*"neural_network" + 0.003*"this_position" + 0.003*"artificial_intelligence" + 0.003*"team_member" + 0.003*"data_mining" + 0.003*"this_role" + 0.002*"health" + 0.002*"data_visualization" + 0.002*"problem_solving"
2019-02-14 22:28:59,057 : INFO : topic #2 (0.140): 0.005*"least_year" + 0.005*"apache_spark" + 0.003*"open_source" + 0.003*"apache" + 0.003*"more_than" + 0.002*"each_other" + 0.002*"this_role" + 0.002*"software_engineer" + 0.002*"software_development" + 0.002*"capital"
2019-02-14 22:28:59,059 : INFO : topic #3 (0.311): 0.006*"neural_network" + 0.006*"data_scientist" + 0.006*"large_scale" + 0.005*"software_development" + 0.005*"software_engineer" + 0.004*"artificial_intelligence" + 0.004*"cutting_edge" + 0.004*"next_generation" + 0.004*"data_set" + 0.004*"google"
2019-02-14 22:28:59,060 : INFO : topic #4 (0.190): 0.004*"this_position" + 0.003*"veteran_status" + 0.003*"microsoft" + 0.003*"computer_vi

2019-02-14 22:29:05,187 : INFO : topic #4 (0.204): 0.004*"veteran_status" + 0.004*"this_position" + 0.004*"applicant_will" + 0.004*"microsoft" + 0.004*"without_regard" + 0.004*"qualified_applicant" + 0.003*"receive" + 0.003*"will_receive" + 0.003*"receive_consideration" + 0.003*"consideration_employment"
2019-02-14 22:29:05,188 : INFO : topic diff=0.324101, rho=0.326129
2019-02-14 22:29:06,289 : INFO : -8.465 per-word bound, 353.2 perplexity estimate based on a held-out corpus of 500 documents with 210703 words
2019-02-14 22:29:06,290 : INFO : PROGRESS: pass 1, at document #3000/3701
2019-02-14 22:29:06,817 : INFO : optimized alpha [0.12636903, 0.5161844, 0.19422674, 0.37025574, 0.22304845]
2019-02-14 22:29:06,818 : INFO : merging changes from 500 documents into a model of 3701 documents
2019-02-14 22:29:06,825 : INFO : topic #0 (0.126): 0.006*"others" + 0.005*"understand_speech" + 0.005*"rule" + 0.003*"word" + 0.003*"comprehension" + 0.003*"information_idea" + 0.003*"appropriate" + 0.

2019-02-14 22:29:11,590 : INFO : topic #0 (0.099): 0.006*"others" + 0.004*"rule" + 0.004*"understand_speech" + 0.003*"word" + 0.003*"appropriate" + 0.002*"information_idea" + 0.002*"general" + 0.002*"duty" + 0.002*"writing" + 0.002*"specific"
2019-02-14 22:29:11,591 : INFO : topic #1 (0.699): 0.005*"data_scientist" + 0.004*"data_mining" + 0.004*"this_position" + 0.003*"advanced_analytics" + 0.003*"pattern_recognition" + 0.003*"neural_network" + 0.003*"health" + 0.003*"data_visualization" + 0.003*"problem_solving" + 0.002*"team_member"
2019-02-14 22:29:11,593 : INFO : topic #2 (0.176): 0.005*"least_year" + 0.004*"apache_spark" + 0.004*"learn_more" + 0.003*"open_source" + 0.003*"apache" + 0.003*"more_than" + 0.003*"this_role" + 0.003*"agile" + 0.003*"capital" + 0.003*"least"
2019-02-14 22:29:11,594 : INFO : topic #3 (0.478): 0.006*"large_scale" + 0.006*"data_scientist" + 0.005*"software_development" + 0.005*"neural_network" + 0.005*"artificial_intelligence" + 0.005*"computer_vision" + 0.

...

2019-02-14 22:31:24,991 : INFO : topic #4 (0.172): 0.006*"employer_qualified" + 0.006*"receive_consideration" + 0.006*"applicant_will" + 0.005*"microsoft" + 0.005*"employment_without" + 0.005*"physical" + 0.005*"reasonable_accommodation" + 0.005*"receive" + 0.005*"accommodation" + 0.005*"care"
2019-02-14 22:31:24,992 : INFO : topic diff=0.126660, rho=0.198411
2019-02-14 22:31:25,954 : INFO : -8.063 per-word bound, 267.5 perplexity estimate based on a held-out corpus of 500 documents with 210703 words
2019-02-14 22:31:25,955 : INFO : PROGRESS: pass 17, at document #3000/3701
2019-02-14 22:31:26,289 : INFO : optimized alpha [0.099630654, 0.58886, 0.29063946, 0.49054402, 0.17470469]
2019-02-14 22:31:26,290 : INFO : merging changes from 500 documents into a model of 3701 documents
2019-02-14 22:31:26,297 : INFO : topic #0 (0.100): 0.007*"others" + 0.005*"understand_speech" + 0.005*"rule" + 0.004*"word" + 0.003*"appropriate" + 0.003*"comprehension" + 0.003*"writing" + 0.003*"general" + 0.00

2019-02-14 22:31:30,073 : INFO : merging changes from 500 documents into a model of 3701 documents
2019-02-14 22:31:30,080 : INFO : topic #0 (0.093): 0.007*"others" + 0.005*"rule" + 0.004*"understand_speech" + 0.004*"appropriate" + 0.003*"word" + 0.003*"general" + 0.003*"comprehension" + 0.003*"writing" + 0.003*"information_idea" + 0.003*"duty"
2019-02-14 22:31:30,081 : INFO : topic #1 (0.735): 0.007*"data_scientist" + 0.005*"this_position" + 0.004*"data_mining" + 0.004*"data_set" + 0.003*"neural_network" + 0.003*"pattern_recognition" + 0.003*"health" + 0.003*"advanced_analytics" + 0.003*"mining" + 0.003*"problem_solving"
2019-02-14 22:31:30,083 : INFO : topic #2 (0.268): 0.006*"apache_spark" + 0.005*"least_year" + 0.005*"apache" + 0.004*"software_development" + 0.004*"best_practice" + 0.004*"this_role" + 0.004*"open_source" + 0.004*"agile" + 0.004*"enterprise" + 0.003*"real_time"
2019-02-14 22:31:30,085 : INFO : topic #3 (0.586): 0.008*"artificial_intelligence" + 0.007*"large_scale" +

2019-02-14 22:31:34,614 : INFO : topic #3 (0.493): 0.007*"large_scale" + 0.007*"artificial_intelligence" + 0.007*"speech_recognition" + 0.006*"software_development" + 0.005*"cutting_edge" + 0.005*"computer_vision" + 0.005*"software_engineer" + 0.004*"next_generation" + 0.004*"familiarity_with" + 0.004*"real_time"
2019-02-14 22:31:34,616 : INFO : topic #4 (0.174): 0.006*"equipment" + 0.005*"physical" + 0.005*"care" + 0.005*"guest" + 0.004*"microsoft" + 0.004*"employer_qualified" + 0.004*"applicant_will" + 0.004*"receive_consideration" + 0.004*"physical_mental" + 0.004*"customer_worker"
2019-02-14 22:31:34,617 : INFO : topic diff=0.283064, rho=0.194617
2019-02-14 22:31:35,360 : INFO : -8.324 per-word bound, 320.6 perplexity estimate based on a held-out corpus of 500 documents with 142768 words
2019-02-14 22:31:35,360 : INFO : PROGRESS: pass 18, at document #3500/3701
2019-02-14 22:31:35,687 : INFO : optimized alpha [0.098479256, 0.6312542, 0.28311515, 0.5261805, 0.17829673]
2019-02-14 22

2019-02-14 22:31:39,019 : INFO : -8.383 per-word bound, 333.9 perplexity estimate based on a held-out corpus of 500 documents with 116221 words
2019-02-14 22:31:39,020 : INFO : PROGRESS: pass 19, at document #1500/3701
2019-02-14 22:31:39,331 : INFO : optimized alpha [0.092454724, 0.7663623, 0.28025126, 0.63920826, 0.17518793]
2019-02-14 22:31:39,333 : INFO : merging changes from 500 documents into a model of 3701 documents
2019-02-14 22:31:39,339 : INFO : topic #0 (0.092): 0.007*"others" + 0.004*"rule" + 0.004*"understand_speech" + 0.004*"appropriate" + 0.003*"word" + 0.003*"general" + 0.003*"writing" + 0.003*"comprehension" + 0.003*"information_idea" + 0.003*"duty"
2019-02-14 22:31:39,341 : INFO : topic #1 (0.766): 0.007*"data_scientist" + 0.005*"this_position" + 0.004*"data_mining" + 0.004*"data_set" + 0.003*"health" + 0.003*"neural_network" + 0.003*"mining" + 0.003*"advanced_analytics" + 0.003*"problem_solving" + 0.003*"data_visualization"
2019-02-14 22:31:39,343 : INFO : topic #2 

2019-02-14 22:31:43,800 : INFO : topic #1 (0.633): 0.007*"data_scientist" + 0.005*"this_position" + 0.004*"data_set" + 0.004*"data_mining" + 0.003*"neural_network" + 0.003*"health" + 0.003*"data_visualization" + 0.003*"advanced_analytics" + 0.002*"problem_solving" + 0.002*"predictive"
2019-02-14 22:31:43,802 : INFO : topic #2 (0.285): 0.009*"apache_spark" + 0.007*"apache" + 0.005*"least_year" + 0.005*"software_development" + 0.004*"open_source" + 0.004*"best_practice" + 0.004*"agile" + 0.004*"this_role" + 0.003*"real_time" + 0.003*"enterprise"
2019-02-14 22:31:43,804 : INFO : topic #3 (0.528): 0.008*"artificial_intelligence" + 0.007*"large_scale" + 0.006*"computer_vision" + 0.006*"software_development" + 0.006*"speech_recognition" + 0.006*"cutting_edge" + 0.005*"neural_network" + 0.005*"software_engineer" + 0.004*"next_generation" + 0.004*"familiarity_with"
2019-02-14 22:31:43,806 : INFO : topic #4 (0.178): 0.006*"care" + 0.005*"equipment" + 0.005*"physical" + 0.004*"resident" + 0.004*

In [68]:
# Print the Keyword in the 5 topics
print(lda_model.print_topics())

2019-02-14 22:31:44,265 : INFO : topic #0 (0.096): 0.007*"others" + 0.005*"understand_speech" + 0.005*"rule" + 0.003*"appropriate" + 0.003*"word" + 0.003*"comprehension" + 0.003*"writing" + 0.003*"general" + 0.003*"complex_problem" + 0.003*"reasoning"
2019-02-14 22:31:44,267 : INFO : topic #1 (0.651): 0.007*"data_scientist" + 0.005*"this_position" + 0.004*"neural_network" + 0.004*"data_set" + 0.004*"data_mining" + 0.003*"advanced_analytics" + 0.003*"health" + 0.003*"problem_solving" + 0.003*"team_member" + 0.002*"data_visualization"
2019-02-14 22:31:44,278 : INFO : topic #2 (0.266): 0.008*"apache_spark" + 0.007*"apache" + 0.005*"least_year" + 0.005*"software_development" + 0.004*"best_practice" + 0.004*"open_source" + 0.004*"agile" + 0.004*"this_role" + 0.003*"enterprise" + 0.003*"real_time"
2019-02-14 22:31:44,280 : INFO : topic #3 (0.564): 0.008*"artificial_intelligence" + 0.007*"computer_vision" + 0.007*"neural_network" + 0.006*"large_scale" + 0.006*"cutting_edge" + 0.006*"software_

[(0, '0.007*"others" + 0.005*"understand_speech" + 0.005*"rule" + 0.003*"appropriate" + 0.003*"word" + 0.003*"comprehension" + 0.003*"writing" + 0.003*"general" + 0.003*"complex_problem" + 0.003*"reasoning"'), (1, '0.007*"data_scientist" + 0.005*"this_position" + 0.004*"neural_network" + 0.004*"data_set" + 0.004*"data_mining" + 0.003*"advanced_analytics" + 0.003*"health" + 0.003*"problem_solving" + 0.003*"team_member" + 0.002*"data_visualization"'), (2, '0.008*"apache_spark" + 0.007*"apache" + 0.005*"least_year" + 0.005*"software_development" + 0.004*"best_practice" + 0.004*"open_source" + 0.004*"agile" + 0.004*"this_role" + 0.003*"enterprise" + 0.003*"real_time"'), (3, '0.008*"artificial_intelligence" + 0.007*"computer_vision" + 0.007*"neural_network" + 0.006*"large_scale" + 0.006*"cutting_edge" + 0.006*"software_development" + 0.005*"speech_recognition" + 0.004*"familiarity_with" + 0.004*"real_time" + 0.004*"software_engineer"'), (4, '0.005*"care" + 0.005*"equipment" + 0.005*"physica

In [69]:
# Compute Coherence Score using c_v
coherence_model_lda = CoherenceModel(model=lda_model, texts=docs, dictionary=dictionary, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)

2019-02-14 22:31:44,294 : INFO : using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
2019-02-14 22:31:44,360 : INFO : 1 batches submitted to accumulate stats from 64 documents (17586 virtual)
2019-02-14 22:31:44,385 : INFO : 2 batches submitted to accumulate stats from 128 documents (39826 virtual)
2019-02-14 22:31:44,404 : INFO : 3 batches submitted to accumulate stats from 192 documents (60879 virtual)
2019-02-14 22:31:44,459 : INFO : 4 batches submitted to accumulate stats from 256 documents (81284 virtual)
2019-02-14 22:31:44,488 : INFO : 5 batches submitted to accumulate stats from 320 documents (104393 virtual)
2019-02-14 22:31:44,509 : INFO : 6 batches submitted to accumulate stats from 384 documents (126259 virtual)
2019-02-14 22:31:44,902 : INFO : 7 batches submitted to accumulate stats from 448 documents (148644 virtual)
2019-02-14 22:31:45,031 : INFO : 8 batches submitted to accumulate stats from 512 documents (1


Coherence Score:  0.45837713424938087


In [70]:
# Compute Coherence Score using UMass
coherence_model_lda = CoherenceModel(model=lda_model, texts=docs, dictionary=dictionary, coherence="u_mass")
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)

2019-02-14 22:32:01,480 : INFO : CorpusAccumulator accumulated stats from 1000 documents
2019-02-14 22:32:01,520 : INFO : CorpusAccumulator accumulated stats from 2000 documents
2019-02-14 22:32:01,567 : INFO : CorpusAccumulator accumulated stats from 3000 documents



Coherence Score:  -1.622346382993245


In [71]:
def compute_coherence_values(dictionary, corpus, texts, limit, start=2, step=3):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        model=LdaModel(corpus=corpus, id2word=dictionary, num_topics=num_topics)
        model_list.append(model)
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values

model_list, coherence_values = compute_coherence_values(dictionary=dictionary, corpus=corpus, texts=docs, start=2, limit=40, step=6)


2019-02-14 22:32:01,643 : INFO : using symmetric alpha at 0.5
2019-02-14 22:32:01,645 : INFO : using symmetric eta at 0.5
2019-02-14 22:32:01,648 : INFO : using serial LDA version on this node
2019-02-14 22:32:01,652 : INFO : running online (single-pass) LDA training, 2 topics, 1 passes over the supplied corpus of 3701 documents, updating model once every 2000 documents, evaluating perplexity every 3701 documents, iterating 50x with a convergence threshold of 0.001000
2019-02-14 22:32:01,653 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2019-02-14 22:32:01,659 : INFO : PROGRESS: pass 0, at document #2000/3701
2019-02-14 22:32:03,859 : INFO : merging changes from 2000 documents into a model of 3701 documents
2019-02-14 22:32:03,862 : INFO : topic #0 (0.500): 0.004*"data_scientist" + 0.003*"data_mining" + 0.003*"artificial_intelligence" + 0.002*"problem_solving" + 0.002*"large_scale" + 0.002*"this_posi

2019-02-14 22:32:18,461 : INFO : 52 batches submitted to accumulate stats from 3328 documents (1361291 virtual)
2019-02-14 22:32:18,512 : INFO : 53 batches submitted to accumulate stats from 3392 documents (1384476 virtual)
2019-02-14 22:32:18,845 : INFO : 54 batches submitted to accumulate stats from 3456 documents (1408090 virtual)
2019-02-14 22:32:18,877 : INFO : 55 batches submitted to accumulate stats from 3520 documents (1427873 virtual)
2019-02-14 22:32:19,063 : INFO : 56 batches submitted to accumulate stats from 3584 documents (1447121 virtual)
2019-02-14 22:32:19,643 : INFO : serializing accumulator to return to master...
2019-02-14 22:32:19,658 : INFO : serializing accumulator to return to master...
2019-02-14 22:32:19,655 : INFO : accumulator serialized
2019-02-14 22:32:19,677 : INFO : accumulator serialized
2019-02-14 22:32:19,809 : INFO : serializing accumulator to return to master...
2019-02-14 22:32:19,821 : INFO : accumulator serialized
2019-02-14 22:32:19,863 : INFO :

2019-02-14 22:32:32,890 : INFO : 27 batches submitted to accumulate stats from 1728 documents (639023 virtual)
2019-02-14 22:32:33,391 : INFO : 28 batches submitted to accumulate stats from 1792 documents (659414 virtual)
2019-02-14 22:32:33,415 : INFO : 29 batches submitted to accumulate stats from 1856 documents (687023 virtual)
2019-02-14 22:32:33,453 : INFO : 30 batches submitted to accumulate stats from 1920 documents (710518 virtual)
2019-02-14 22:32:34,070 : INFO : 31 batches submitted to accumulate stats from 1984 documents (731671 virtual)
2019-02-14 22:32:34,105 : INFO : 32 batches submitted to accumulate stats from 2048 documents (753474 virtual)
2019-02-14 22:32:34,229 : INFO : 33 batches submitted to accumulate stats from 2112 documents (776202 virtual)
2019-02-14 22:32:34,640 : INFO : 34 batches submitted to accumulate stats from 2176 documents (802076 virtual)
2019-02-14 22:32:34,881 : INFO : 35 batches submitted to accumulate stats from 2240 documents (829037 virtual)
2

2019-02-14 22:32:51,821 : INFO : topic diff=2.203426, rho=0.707107
2019-02-14 22:32:51,832 : INFO : using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
2019-02-14 22:32:51,888 : INFO : 1 batches submitted to accumulate stats from 64 documents (17586 virtual)
2019-02-14 22:32:51,906 : INFO : 2 batches submitted to accumulate stats from 128 documents (39826 virtual)
2019-02-14 22:32:51,929 : INFO : 3 batches submitted to accumulate stats from 192 documents (60879 virtual)
2019-02-14 22:32:51,978 : INFO : 4 batches submitted to accumulate stats from 256 documents (81284 virtual)
2019-02-14 22:32:52,008 : INFO : 5 batches submitted to accumulate stats from 320 documents (104393 virtual)
2019-02-14 22:32:52,029 : INFO : 6 batches submitted to accumulate stats from 384 documents (125865 virtual)
2019-02-14 22:32:52,465 : INFO : 7 batches submitted to accumulate stats from 448 documents (148511 virtual)
2019-02-14 22:32:52,565 : I

2019-02-14 22:33:11,426 : INFO : topic #11 (0.050): 0.003*"data_mining" + 0.003*"large_scale" + 0.003*"cutting_edge" + 0.003*"problem_solving" + 0.003*"related_field" + 0.002*"data_scientist" + 0.002*"artificial_intelligence" + 0.002*"programming_language" + 0.002*"this_role" + 0.002*"software_development"
2019-02-14 22:33:11,427 : INFO : topic #5 (0.050): 0.004*"team_member" + 0.004*"this_position" + 0.003*"financial" + 0.003*"sale" + 0.003*"more_than" + 0.002*"artificial_intelligence" + 0.002*"united_state" + 0.002*"data_scientist" + 0.002*"real_time" + 0.002*"this_role"
2019-02-14 22:33:11,429 : INFO : topic #17 (0.050): 0.007*"data_scientist" + 0.004*"this_role" + 0.003*"this_position" + 0.003*"pattern_recognition" + 0.003*"data_visualization" + 0.003*"related_field" + 0.003*"master_degree" + 0.002*"data_mining" + 0.002*"team_member" + 0.002*"work_closely"
2019-02-14 22:33:11,431 : INFO : topic #2 (0.050): 0.004*"this_position" + 0.002*"data_scientist" + 0.002*"data_set" + 0.002*"f

2019-02-14 22:33:30,661 : INFO : 47 batches submitted to accumulate stats from 3008 documents (1210921 virtual)
2019-02-14 22:33:31,039 : INFO : 48 batches submitted to accumulate stats from 3072 documents (1243329 virtual)
2019-02-14 22:33:31,419 : INFO : 49 batches submitted to accumulate stats from 3136 documents (1271518 virtual)
2019-02-14 22:33:32,168 : INFO : 50 batches submitted to accumulate stats from 3200 documents (1301991 virtual)
2019-02-14 22:33:32,603 : INFO : 51 batches submitted to accumulate stats from 3264 documents (1320044 virtual)
2019-02-14 22:33:33,189 : INFO : 52 batches submitted to accumulate stats from 3328 documents (1338918 virtual)
2019-02-14 22:33:33,720 : INFO : 53 batches submitted to accumulate stats from 3392 documents (1362739 virtual)
2019-02-14 22:33:33,841 : INFO : 54 batches submitted to accumulate stats from 3456 documents (1384264 virtual)
2019-02-14 22:33:34,153 : INFO : 55 batches submitted to accumulate stats from 3520 documents (1407618 v

2019-02-14 22:33:50,984 : INFO : 20 batches submitted to accumulate stats from 1280 documents (469212 virtual)
2019-02-14 22:33:51,077 : INFO : 21 batches submitted to accumulate stats from 1344 documents (488877 virtual)
2019-02-14 22:33:51,591 : INFO : 22 batches submitted to accumulate stats from 1408 documents (511495 virtual)
2019-02-14 22:33:51,652 : INFO : 23 batches submitted to accumulate stats from 1472 documents (531921 virtual)
2019-02-14 22:33:52,002 : INFO : 24 batches submitted to accumulate stats from 1536 documents (552966 virtual)
2019-02-14 22:33:52,276 : INFO : 25 batches submitted to accumulate stats from 1600 documents (575653 virtual)
2019-02-14 22:33:52,372 : INFO : 26 batches submitted to accumulate stats from 1664 documents (609431 virtual)
2019-02-14 22:33:52,662 : INFO : 27 batches submitted to accumulate stats from 1728 documents (635463 virtual)
2019-02-14 22:33:53,017 : INFO : 28 batches submitted to accumulate stats from 1792 documents (655896 virtual)
2

2019-02-14 22:34:18,507 : INFO : topic #2 (0.031): 0.008*"both_current" + 0.004*"ability_tell" + 0.004*"transportation_provided" + 0.003*"mortgage" + 0.003*"normal_office" + 0.003*"associate_gain" + 0.002*"more_than" + 0.002*"loan" + 0.002*"care" + 0.002*"this_position"
2019-02-14 22:34:18,509 : INFO : topic #28 (0.031): 0.008*"neural_network" + 0.003*"artificial_intelligence" + 0.003*"software_development" + 0.003*"this_position" + 0.002*"related_field" + 0.002*"least_year" + 0.002*"data_scientist" + 0.002*"communication_skill" + 0.002*"supply_chain" + 0.002*"career"
2019-02-14 22:34:18,512 : INFO : topic diff=4.387393, rho=0.707107
2019-02-14 22:34:18,523 : INFO : using ParallelWordOccurrenceAccumulator(processes=3, batch_size=64) to estimate probabilities from sliding windows
2019-02-14 22:34:18,578 : INFO : 1 batches submitted to accumulate stats from 64 documents (17586 virtual)
2019-02-14 22:34:18,597 : INFO : 2 batches submitted to accumulate stats from 128 documents (39826 virt

2019-02-14 22:34:41,993 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2019-02-14 22:34:41,997 : INFO : PROGRESS: pass 0, at document #2000/3701
2019-02-14 22:34:44,973 : INFO : merging changes from 2000 documents into a model of 3701 documents
2019-02-14 22:34:45,005 : INFO : topic #2 (0.026): 0.004*"open_source" + 0.004*"financial" + 0.003*"software_development" + 0.003*"artificial_intelligence" + 0.002*"cross_functional" + 0.002*"apache_spark" + 0.002*"financial_service" + 0.002*"this_role" + 0.002*"agile" + 0.002*"pattern_recognition"
2019-02-14 22:34:45,007 : INFO : topic #18 (0.026): 0.004*"this_position" + 0.004*"more_than" + 0.003*"real_time" + 0.003*"fast_paced" + 0.003*"data_scientist" + 0.003*"least_year" + 0.003*"apache_spark" + 0.002*"internal_external" + 0.002*"data_set" + 0.002*"health"
2019-02-14 22:34:45,008 : INFO : topic #26 (0.026): 0.004*"pattern_recognition" + 0.003*"this_positio

2019-02-14 22:35:05,010 : INFO : 41 batches submitted to accumulate stats from 2624 documents (997634 virtual)
2019-02-14 22:35:05,088 : INFO : 42 batches submitted to accumulate stats from 2688 documents (1031338 virtual)
2019-02-14 22:35:05,586 : INFO : 43 batches submitted to accumulate stats from 2752 documents (1061841 virtual)
2019-02-14 22:35:06,489 : INFO : 44 batches submitted to accumulate stats from 2816 documents (1095657 virtual)
2019-02-14 22:35:07,181 : INFO : 45 batches submitted to accumulate stats from 2880 documents (1130568 virtual)
2019-02-14 22:35:07,869 : INFO : 46 batches submitted to accumulate stats from 2944 documents (1170294 virtual)
2019-02-14 22:35:09,016 : INFO : 47 batches submitted to accumulate stats from 3008 documents (1206962 virtual)
2019-02-14 22:35:09,835 : INFO : 48 batches submitted to accumulate stats from 3072 documents (1240296 virtual)
2019-02-14 22:35:10,188 : INFO : 49 batches submitted to accumulate stats from 3136 documents (1268424 vi

Coherence drops off significantly after 5. So, I will limit the topics there.

## Supervised Approach

### Bag of Words

#### BoW with SKLearn CountVectorizer

In [72]:
#Setting additional stopwords
en_stop = set(nltk.corpus.stopwords.words('english'))
stopwords = en_stop.union(set(['machine','business','analytics','learning','technology',
                              'system']))

In [73]:
tok = WordPunctTokenizer()
pat1 = r'@[A-Za-z0-9]+'
pat2 = r'https?://[A-Za-z0-9./]+'
combined_pat = r'|'.join((pat1, pat2))

def clean_text(text):
    # 1. Remove HTML
    soup = BeautifulSoup(text)
    souped = soup.get_text()
    #
    # 2. Remove non-letters        
    #letters_only = re.sub("[^a-zA-Z]", " ", review_text)
    stripped = re.sub(combined_pat, '', souped)
    try:
        clean = stripped.decode("utf-8-sig").replace(u"\ufffd", "?")
    except:
        clean = stripped
    letters_only = re.sub("[^a-zA-Z]", " ", clean)
    #
    # 3. Convert to lower case, split into individual words
    lower_case = letters_only.lower() 
    words = tok.tokenize(lower_case)
    #
    # 4. In Python, searching a set is much faster than searching
    #   a list, so convert the stop words to a set
    stops = set(stopwords.words("english"))                  
    # 
    # 5. Remove stop words
    meaningful_words = [w for w in words if not w in stops]   
    #
    # 6. Join the words back into one string separated by space, 
    # and return the result.
    #return( " ".join( meaningful_words ))   
    
    return (" ".join(words)).strip()

In [74]:
# remove punctuation from the job titles first
X['job_description'] = X['job_description'].apply(clean_text)

AttributeError: 'set' object has no attribute 'words'

In [ ]:
#split up for classification
y = X.job_class
X1 = X.job_description

In [ ]:
y_train, y_test = train_test_split(y, test_size=0.25, random_state=42)

In [ ]:
vectorizer = CountVectorizer(tokenizer=LemmaTokenizer(), stop_words='english', analyzer='word', 
                            ngram_range=(1, 1), max_df=1.0, min_df=1, max_features=None)
bow = vectorizer.fit_transform(X1)
print(vectorizer.get_feature_names())

In [ ]:
#Split into X_train and X_test now that BoW is complete.
X_train, X_test= train_test_split(bow, test_size=0.25, random_state=42)

### Models to test initial Bag of Words

In [ ]:
start = time.time()

rfc = ensemble.RandomForestClassifier()
fit = rfc.fit(X_train, y_train)
y_pred = rfc.predict(X_test)

print('Training set score:', rfc.score(X_train, y_train))
print('\nTest set score:', rfc.score(X_test, y_test))
end = time.time()
print("Done in", end - start, "seconds")

In [ ]:
# Logistic Regression Classifier
start = time.time()
lr = LogisticRegression()
lr.fit(X_train,y_train)

print('Training set score:', lr.score(X_train, y_train))
print('\nTest set score:', lr.score(X_test, y_test))
end = time.time()
print("Done in", end - start, "seconds")

### K Means

In [ ]:
# Normalize the data.
X_norm = normalize(X_train)

In [ ]:
# Reduce it to two components.
X_pca_bow = PCA(2).fit_transform(X_norm.todense())

# Calculate predicted values.
y_pred = KMeans(n_clusters=9, random_state=42).fit_predict(X_pca_bow)

# Plot the solution.
plt.scatter(X_pca_bow[:, 0], X_pca_bow[:, 1], c=y_pred)
plt.show()

### KMeans Mini-Batch

In [ ]:
X_train_norm = normalize(X_train)
X_test_norm = normalize(X_test)

true_k = 10
km = MiniBatchKMeans(n_clusters=true_k, init='k-means++', batch_size=5000)

km.fit(X_train_norm)
km_train_label = km.labels_
km_test_label = km.predict(X_test_norm)
true_k = 10
km = MiniBatchKMeans(n_clusters=true_k, init='k-means++', batch_size=5000)

km.fit(X_train_norm)
km_train_label = km.labels_
km_test_label = km.predict(X_test_norm)

In [ ]:
from time import time

rfc = ensemble.RandomForestClassifier()
fit = rfc.fit(X_train_norm, y_train)
y_pred = rfc.predict(X_test_norm)

print('Training set score:', rfc.score(X_train_norm, y_train))
print('\nTest set score:', rfc.score(X_test_norm, y_test))
t0 = time()
print("Done in %0.3fs" % (time() - t0))

In [ ]:
# Logistic Regression Classifier
import time
start = time.time()
lr = LogisticRegression()
lr.fit(X_train_norm,y_train)

print('Training set score:', lr.score(X_train_norm, y_train))
print('\nTest set score:', lr.score(X_test_norm, y_test))
end = time.time()
print("Done in", end - start, "seconds")

### LSA with BoW

In [ ]:
# Logistic Regression Classifier
import time
start = time.time()
lr = LogisticRegression()
lr.fit(X_train_norm,y_train)

print('Training set score:', lr.score(X_train_norm, y_train))
print('\nTest set score:', lr.score(X_test_norm, y_test))
end = time.time()
print("Done in", end - start, "seconds")

In [ ]:
start = time.time()
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import Normalizer

from sklearn.decomposition import TruncatedSVD
lsa = TruncatedSVD(n_components=5,n_iter=500)
lsa.fit(bow)
terms = vectorizer.get_feature_names()
X_train_lsa = lsa.fit_transform(X_train)
X_test_lsa = lsa.transform(X_test)

for i,comp in enumerate(lsa.components_):
    termsInComp = zip(terms,comp)
    sortedterms = sorted(termsInComp, key=lambda x: x[1],reverse=True)[:10]
    print("Concept %d:" % i)
    for term in sortedterms:
        print(term[0])
    print(" ")
end = time.time()
print("Done in", end - start, "seconds")

In [ ]:
fit = rfc.fit(X_train_lsa, y_train)
y_pred = rfc.predict(X_test_lsa)

print('Training set score:', rfc.score(X_train_lsa, y_train))
print('\nTest set score:', rfc.score(X_test_lsa, y_test))


### Bigrams

In [ ]:
X_train_clean, X_test_clean= train_test_split(X, test_size=0.25, random_state=42)
count_vect_bigram = CountVectorizer(ngram_range=(1,2))
train_data_bow_bigram = count_vect_bigram.fit_transform(X_train_clean)
test_data_bow_bigram = count_vect_bigram.transform(X_test_clean)

In [ ]:
X_norm = normalize(train_data_bow_bigram)
# Reduce it to two components.
X_pca_bow = PCA(2).fit_transform(X_norm.todense())

# Calculate predicted values.
y_pred = KMeans(n_clusters=9, random_state=42).fit_predict(X_pca_bow)

# Plot the solution.
plt.scatter(X_pca_bow[:, 0], X_pca_bow[:, 1], c=y_pred)
plt.show()

In [ ]:
import time
start = time.time()

#Confusion matrix for Bigram BOW with Logistic Regression

lr = LogisticRegression()
lr.fit(train_data_bow_bigram,y_train)

print('Training set score:', lr.score(train_data_bow_bigram, y_train))
print('\nTest set score:', lr.score(test_data_bow_bigram, y_test))

y_pred = lr.predict(test_data_bow_bigram)

conf = confusion_matrix(y_test, y_pred, labels = X.job_class)

cm = pd.DataFrame(conf, index = [i for i in handles],
                  columns = [i for i in handles])
plt.figure(figsize = (15,7))
plt.title('Confusion Matrix for BoW with Bigrams')
sns.heatmap(cm, annot=True, cmap="PuBu", fmt = 'd')
crs = cross_val_score(lr, train_data_bow_bigram, y_train, cv=10)
print("Cross-Valid Bigram Fold Results are: ",crs)
print("Mean of Folds are = ",crs.mean())
end = time.time()
print("Done in %0.3fs", end - start)

## TF-IDF Analysis

### Train and Test Sets


In [ ]:
tfidf_transformer = TfidfTransformer()
tfidf = tfidf_transformer.fit_transform(bow)
tfidf.shape

In [ ]:
X_train_tfidf, X_test_tfidf = train_test_split(tfidf, test_size=0.25, random_state=42)

In [ ]:
import time

start = time.time()

rfc = ensemble.RandomForestClassifier()
fit = rfc.fit(X_train_tfidf, y_train)
y_pred = rfc.predict(X_test_tfidf)

print('Training set score:', rfc.score(X_train_tfidf, y_train))
print('\nTest set score:', rfc.score(X_test_tfidf, y_test))
end = time.time()
print("Done in", end - start, "seconds")

In [ ]:
# Logistic Regression Classifier
start = time.time()
lr = LogisticRegression()
lr.fit(X_train_tfidf,y_train)

print('Training set score:', lr.score(X_train_tfidf, y_train))
print('\nTest set score:', lr.score(X_test_tfidf, y_test))
end = time.time()
print("Done in", end - start, "seconds")

In [ ]:
start = time.time()
# Normalize the data.
X_normt = normalize(tfidf)
# Reduce it to two components.
X_pcat = PCA(2).fit_transform(X_normt.todense())

# Calculate predicted values.
y_pred = KMeans(n_clusters=2, random_state=42).fit_predict(X_pcat)

# Plot the solution.
plt.scatter(X_pcat[:, 0], X_pcat[:, 1], c=y_pred)
plt.show()
end = time.time()
print("Done in %0.3fs", end - start)

In [ ]:
start = time.time()
rfc = ensemble.RandomForestClassifier()

vectorizer1 = TfidfVectorizer(max_df=0.5, # drop words that occur in more than half the tweets
                             min_df=2, # only use words that appear at least 2x
                             stop_words='english', 
                             lowercase=True, #convert everything to lower case 
                             use_idf=True,
                             norm=u'l2', #Applies a correction factor so that longer paragraphs and shorter tweets get treated equally
                             smooth_idf=True #Adds 1 to all document frequencies, as if an extra document existed that used every word once.  Prevents divide-by-zero errors
                            )

X_train_tfidf = vectorizer1.fit_transform(X_train_clean)
X_test_tfidf = vectorizer1.transform(X_test_clean)

fit = rfc.fit(X_train_tfidf, y_train)
y_pred = rfc.predict(X_test_tfidf)

print('Training set score:', rfc.score(X_train_tfidf, y_train))
print('\nTest set score:', rfc.score(X_test_tfidf, y_test))
end = time.time()
print("Done in %0.3fs", end - start)

In [ ]:
start = time.time()
X = df['Tweets']
X_norm_tfidf = normalize(vectorizer1.fit_transform(X))

true_k = 10
labels = y
km = MiniBatchKMeans(n_clusters=true_k, init='k-means++', batch_size=5000)

print("Clustering sparse data with %s" % km)
km.fit(X_norm_tfidf)
mini_labels = km.labels_
print("Homogeneity: %0.3f" % metrics.homogeneity_score(labels, km.labels_))
print("Completeness: %0.3f" % metrics.completeness_score(labels, km.labels_))
print("V-measure: %0.3f" % metrics.v_measure_score(labels, km.labels_))
print("Adjusted Rand-Index: %.3f"
      % metrics.adjusted_rand_score(labels, km.labels_))
print("Silhouette Coefficient: %0.3f"
      % metrics.silhouette_score(X_norm_tfidf, km.labels_, sample_size=5000))
end = time.time()
print("Done in %0.3fs", end - start)

In [ ]:
df['MiniBatchLabels'] = mini_labels

In [ ]:
for label in set(mini_labels):
    print('Cluster: %d' % label)
    print(df[df.MiniBatchLabels == label].groupby('Org').count())
    print('')

In [ ]:
#Let's check Cluster 0 - the largest, and likely a catch-all for tweets that did not fall into other clusters
shuffle(df[df.MiniBatchLabels == 0]).head(10)

In [ ]:
#Let's check Cluster 1
shuffle(df[df.MiniBatchLabels == 1]).head(10)

In [ ]:
#Cluster 2
shuffle(df[df.MiniBatchLabels == 2]).head(10)

### LSA with TF-IDF

In [ ]:
print("Number of features: %d" % X_train_tfidf.get_shape()[1])

In [ ]:
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import Normalizer

#Our SVD data reducer.  We are going to reduce the feature space to about 10% of the original.
svd= TruncatedSVD(2100)
lsa = make_pipeline(svd, Normalizer(copy=False))
# Run SVD on the training data, then project the training data.
X_train_lsa = lsa.fit_transform(X_train_tfidf)
X_test_lsa = lsa.transform(X_test_tfidf)

variance_explained=svd.explained_variance_ratio_
total_variance = variance_explained.sum()
print("Percent variance captured by all components:",total_variance*100)

#Looking at what sorts of tweets our solution considers similar, for the first five identified topics
tweets_by_component=pd.DataFrame(X_train_lsa, index=list(X_train))
for i in range(5):
    print('Component {}:'.format(i))
    print(tweets_by_component.loc[:,i].sort_values(ascending=False)[0:10])
import time
print(time.time())

In [ ]:
from sklearn.decomposition import TruncatedSVD
lsa = TruncatedSVD(n_components=5,n_iter=500)
lsa.fit(tfidf)
terms = vectorizer.get_feature_names()

for i,comp in enumerate(lsa.components_):
    termsInComp = zip(terms,comp)
    sortedterms = sorted(termsInComp, key=lambda x: x[1],reverse=True)[:10]
    print("Concept %d:" % i)
    for term in sortedterms:
        print(term[0])
    print(" ")

In [ ]:
#Try a GBM classifier here, using TF-IDF 

clf = ensemble.GradientBoostingClassifier()
train = clf.fit(X_train_tfidf, y_train)
tfidf_pred = clf.predict(X_test_tfidf.toarray())

print('Training set score:', clf.score(X_train_tfidf.toarray(), y_train))
print('\nTest set score:', clf.score(X_test_tfidf.toarray(), y_test))

In [ ]:
#Confusion matrix for GBM performance visualization on TF-IDF

conf = confusion_matrix(y_test, tfidf_pred, labels = handles)

df_cm = pd.DataFrame(conf, index = [i for i in handles],
                  columns = [i for i in handles])
plt.figure(figsize = (15,7))
sns.heatmap(df_cm, annot=True, cmap="Blues", fmt = 'd')

In [ ]:
X_train_tfidf.shape

In [ ]:
#LSA with Tf-idf
mlp = neural_network.MLPClassifier(hidden_layer_sizes = (100,), activation = 'logistic')
train = mlp.fit(X_train_lsa, y_train)
mlp_y_pred = mlp.predict(X_test_lsa)

print('Training set score:', mlp.score(X_train_lsa, y_train))
print('\nTest set score:', mlp.score(X_test_lsa, y_test))